To Do:
- Make List page have subpages (e.g., list of forms, list of forms using a field, see below), make these fileres visible after the intro paragraph
- Make list of forms using a given field with description with embeded question bank info

Thought: make a pdf editor the first step in the weaver. Leverage the name normalizer but allow folks to add and remove fields and rename. 

In [1]:
import pandas as pd
import re
#import PyPDF2
import os
from os import walk
import os.path
from os import path
import shutil

import numpy as np

##import time
from datetime import date

from joblib import dump, load

import urllib.parse

In [2]:
import psutil, time

def governor(wait=0,cpu_trigger=55,mem_trigger=66.66,verbose=0):
    wait_tick = 0.01
    cpu = psutil.cpu_percent()
    mem = psutil.virtual_memory().percent
    if verbose==1:
        print("\n=======================================")
        print(" Usage: CPU {}% & Memory {}%".format(cpu,mem))
        
    if (wait<0):
        if verbose==1:
            print("   Full speed ahead!")
        
    elif (wait>(wait_tick*1000)):    
        #if verbose==1:
        print("    Shut it down!!!")
        #display(Javascript('IPython.notebook.save_checkpoint();'))
        time.sleep(5)
        quit()
    
    elif (cpu > cpu_trigger) | (mem > mem_trigger):
        #if verbose==1:
        print("    Slowing down...")
        time.sleep(wait)
        governor(wait+wait_tick)
    
    if verbose==1:
        print("=======================================\n")

In [3]:
governor(0,55,66.66,1)


 Usage: CPU 11.8% & Memory 59.9%



In [4]:
%%time
import formfyxer as lit

CPU times: user 3.84 s, sys: 759 ms, total: 4.6 s
Wall time: 38.5 s


In [5]:
def removeSpecial(text):
    text = re.sub('[^a-zA-Z0-9]',"_",text)
    return re.sub('_+',"_",text)

In [6]:
def clean_n(n):
    if pd.notnull(n):
        return int(n)
    else:
        return 0

In [7]:
today = date.today().strftime("%Y-%m-%d")

## Old data

In [8]:
%%time
files_df_old = pd.read_csv("../data/processed/form_data.csv")
print(len(files_df_old))
display(files_df_old[:2])
files_df_old.columns

10281


id jurisdiction  \
0  04b3a0734774c02edf8eb9056d23954aa38e96c77c3392...           UT   
1  6e420f1b3575cfd8ef94b71977da9e38252e3395a78439...           UT   

             source                                              title  \
0  www.utcourts.gov  Community Service Worksheet Third District Juv...   
1  www.utcourts.gov  Third District Juvenile Court Work Program Ref...   

                                              group  \
0  3rd District Juvenile Court: Forms and Pamphlets   
1  3rd District Juvenile Court: Forms and Pamphlets   

                                                 url  \
0  https://www.utcourts.gov/courts/juv/juvsites/3...   
1  https://www.utcourts.gov/courts/juv/juvsites/3...   

                                            filename  downloaded  pages  \
0  COMMUNITY%20SERVICE%20WORKSHEET-FRONT%20AND%20...  2021-11-11    2.0   
1                     Work_Crew_Application-2007.pdf  2021-11-11    2.0   

                                              fields  \
0  ['name__1', 'name__2', '*docket_number', '*use...   
1  ['*docket_number', '*users1_birthdate', 'male'...   

                                         fields_conf  \
0  [0.63, 0.61, 1, 1, 1, 0.61, 0.52, 0.53, 0.6, 0...   
1  [1, 1, 0.69, 0.61, 1, 1, 1, 0.56, 0.68, 0.67, ...   

                                          fields_old  f_per_p  reading  \
0  ['name__1', 'name__2', 'docket_number', 'users...      7.5     10.5   
1  ['docket_number', 'users1_birthdate', 'male', ...     19.0     10.5   

                 list                                               text  \
0                  []  COMMUNITY SERVICE WORKSHEET\n THIRD DISTRICT J...   
1  ['GO-00-00-00-00']  THIRD DISTRICT JUVENILE COURT WORK PROGRAM REF...   

  downloaded_on  
0           NaN  
1           NaN

CPU times: user 446 ms, sys: 93.2 ms, total: 539 ms
Wall time: 2.25 s


Index(['id', 'jurisdiction', 'source', 'title', 'group', 'url', 'filename',
       'downloaded', 'pages', 'fields', 'fields_conf', 'fields_old', 'f_per_p',
       'reading', 'list', 'text', 'downloaded_on'],
      dtype='object')

In [9]:
%%time
form_sim_data_old = pd.read_csv("../data/processed/form_sim_data.csv")
print(len(form_sim_data_old))
display(form_sim_data_old[:2])
form_sim_data_old.columns

3162622


id_1  \
0  e12318ce9037e92ee8e48963f550e1a3229a17a2437b9e...   
1  e12318ce9037e92ee8e48963f550e1a3229a17a2437b9e...   

                                                id_2  \
0  eb4e35c3b9f355d63ad14ae71866d44b14e61196763553...   
1  74723a905136a3e30a9eec9aa9191f5d3e4b800ae319df...   

                                             title_2  similarity  
0  Answer to Complaint to Recover Possession of P...    0.979167  
1  Answer, Damage/Health Hazard to Property, Land...    0.937500

CPU times: user 2.74 s, sys: 286 ms, total: 3.02 s
Wall time: 6.19 s


Index(['id_1', 'id_2', 'title_2', 'similarity'], dtype='object')

## New Dats

In [10]:
csv_path = "../data/state_forms/"

In [11]:
%%time
forms_df = pd.read_csv(csv_path+"form_data.csv", index_col=0, encoding="utf-8")
forms_df["id"] = forms_df.index

print(len(forms_df))
display(forms_df[:2])
forms_df.columns

30871


jurisdiction        source  group title  \
ce7ec7991f0283ea319598ff05183e50           MA  www.mass.gov    NaN    \n   
13c091b90b3ee286afef69e55591d6f9           MA  www.mass.gov    NaN    \n   

                                                                                url  \
ce7ec7991f0283ea319598ff05183e50  https://www.mass.gov/doc/order-to-render-mpc-7...   
13c091b90b3ee286afef69e55591d6f9  https://www.mass.gov/doc/trust-account-mpc-859...   

                                   filename  downloaded  \
ce7ec7991f0283ea319598ff05183e50  /download           1   
13c091b90b3ee286afef69e55591d6f9  /download           1   

                                                                id  
ce7ec7991f0283ea319598ff05183e50  ce7ec7991f0283ea319598ff05183e50  
13c091b90b3ee286afef69e55591d6f9  13c091b90b3ee286afef69e55591d6f9

CPU times: user 101 ms, sys: 11 ms, total: 112 ms
Wall time: 263 ms


Index(['jurisdiction', 'source', 'group', 'title', 'url', 'filename',
       'downloaded', 'id'],
      dtype='object')

In [12]:
%%time
forms_df_sup_1 = pd.read_csv(csv_path+"form_scratch_x_1_spot.csv", index_col=0, encoding="utf-8")

CPU times: user 1.01 s, sys: 207 ms, total: 1.21 s
Wall time: 10.1 s


In [13]:
%%time
forms_df_sup_2 = pd.read_csv(csv_path+"form_scratch_x_2_spot.csv", index_col=0, encoding="utf-8")

CPU times: user 1.01 s, sys: 229 ms, total: 1.24 s
Wall time: 8.03 s


In [14]:
%%time
forms_df_sup_3 = pd.read_csv(csv_path+"form_scratch_x_3_spot.csv", index_col=0, encoding="utf-8")

CPU times: user 1.06 s, sys: 191 ms, total: 1.25 s
Wall time: 3.92 s


In [15]:
forms_df_sup = pd.concat([forms_df_sup_1,forms_df_sup_2,forms_df_sup_3])
#forms_df_sup = forms_df_sup_1.copy()

forms_df_sup.index = forms_df_sup.index.str.replace(r'\.pdf$', '', regex=True)
forms_df_sup = forms_df_sup.rename(columns={"title":"meta title"})
forms_df_sup["id"] = forms_df_sup.index
forms_df_sup = forms_df_sup.reset_index()
forms_df_sup = forms_df_sup.drop_duplicates(subset=["id"])

print(len(forms_df_sup))
display(forms_df_sup[:2])
forms_df_sup.columns

24062


index  \
0  9fffe321a9fbafdb7964293e8c88e265   
1  9ffd35f8778e21212dd0f319ebb497d2   

                                          meta title  suggested title  \
0                                 Writ of Possession              NaN   
1  Instructions For Florida Supreme Court Approve...              NaN   

   description  category  pages reading grade level time to answer  \
0          NaN       NaN    2.0                  13     [5.3, 1.9]   
1          NaN       NaN    9.0                  20    [83.0, 9.7]   

                                   list avg fields per page  ...  \
0                    ['GO-00-00-00-00']                 5.5  ...   
1  ['ES-00-00-00-00', 'FA-00-00-00-00']            7.888889  ...   

  passive voice percent citations per field citation count  all caps percent  \
0              0.222222            0.090909            1.0          0.021858   
1              0.217391            0.000000            0.0          0.038889   

                                     difficult words difficult word count  \
0  ['numbers', 'reprographics', 'applicable', 'at...                 59.0   
1  ['related', 'special', 'dissolution', 'initial...                243.0   

  difficult word percent calculation required  \
0               0.161202                False   
1               0.071053                False   

                                           full_text  \
0  Writ  of Possession \n\n \n\nin  the District ...   
1  INSTRUCTIONS FOR FLORIDA SUPREME COURT APPROVE...   

                                 id  
0  9fffe321a9fbafdb7964293e8c88e265  
1  9ffd35f8778e21212dd0f319ebb497d2  

[2 rows x 34 columns]

Index(['index', 'meta title', 'suggested title', 'description', 'category',
       'pages', 'reading grade level', 'time to answer', 'list',
       'avg fields per page', 'fields', 'fields_conf', 'fields_old',
       'number of sentences', 'sentences per page',
       'number of passive voice sentences', 'passive sentences',
       'number of all caps words', 'citations', 'total fields',
       'slotin percent', 'gathered percent', 'created percent',
       'third party percent', 'passive voice percent', 'citations per field',
       'citation count', 'all caps percent', 'difficult words',
       'difficult word count', 'difficult word percent',
       'calculation required', 'full_text', 'id'],
      dtype='object')

In [16]:
forms_df_merged = forms_df.merge(forms_df_sup, on="id", how="right")
print(len(forms_df_merged))
display(forms_df_merged[:2])
forms_df_merged.columns

24062


jurisdiction                  source  group               title  \
0           HI  www.courts.state.hi.us    NaN  Writ of Possession   
1           FL        www.flcourts.gov    NaN                  \n   

                                                 url        filename  \
0  https://www.courts.state.hi.us/docs/form/kauai...       5DC54.pdf   
1  https://www.flcourts.gov/content/download/6859...  970%28b%29.pdf   

   downloaded                                id  \
0         1.0  9fffe321a9fbafdb7964293e8c88e265   
1         1.0  9ffd35f8778e21212dd0f319ebb497d2   

                              index  \
0  9fffe321a9fbafdb7964293e8c88e265   
1  9ffd35f8778e21212dd0f319ebb497d2   

                                          meta title  ...  \
0                                 Writ of Possession  ...   
1  Instructions For Florida Supreme Court Approve...  ...   

   third party percent  passive voice percent  citations per field  \
0                  0.0               0.222222             0.090909   
1                  0.0               0.217391             0.000000   

   citation count all caps percent  \
0             1.0         0.021858   
1             0.0         0.038889   

                                     difficult words difficult word count  \
0  ['numbers', 'reprographics', 'applicable', 'at...                 59.0   
1  ['related', 'special', 'dissolution', 'initial...                243.0   

  difficult word percent calculation required  \
0               0.161202                False   
1               0.071053                False   

                                           full_text  
0  Writ  of Possession \n\n \n\nin  the District ...  
1  INSTRUCTIONS FOR FLORIDA SUPREME COURT APPROVE...  

[2 rows x 41 columns]

Index(['jurisdiction', 'source', 'group', 'title', 'url', 'filename',
       'downloaded', 'id', 'index', 'meta title', 'suggested title',
       'description', 'category', 'pages', 'reading grade level',
       'time to answer', 'list', 'avg fields per page', 'fields',
       'fields_conf', 'fields_old', 'number of sentences',
       'sentences per page', 'number of passive voice sentences',
       'passive sentences', 'number of all caps words', 'citations',
       'total fields', 'slotin percent', 'gathered percent', 'created percent',
       'third party percent', 'passive voice percent', 'citations per field',
       'citation count', 'all caps percent', 'difficult words',
       'difficult word count', 'difficult word percent',
       'calculation required', 'full_text'],
      dtype='object')

In [17]:
def count_characters(text):
    return len(str(text))

In [18]:
forms_df_merged["downloaded"]= "2023-03"

In [19]:
csv_df = forms_df_merged.copy()

In [20]:
files_df_old["title_old"] = files_df_old["title"]
len(files_df_old)

10281

In [21]:
csv_df = csv_df.merge(files_df_old[["id","title_old"]], how="left")#.reset_index()
csv_df["title_old"] = csv_df["title_old"].fillna("")


In [22]:
#csv_df.drop_duplicates(inplace=True)

In [23]:
csv_df["title_old_count"] = None
csv_df["title_count"] = None
csv_df["meta_title_count"] = None
csv_df["title_old_count"] = csv_df["title_old"].apply(count_characters)
csv_df["title_count"] = csv_df["title"].apply(count_characters)
csv_df["meta_title_count"] = csv_df["meta title"].apply(count_characters)

In [24]:
csv_df.loc[(csv_df["title_count"]<10),"title"] = csv_df["meta title"]
csv_df.loc[pd.isnull(csv_df["title_count"]),"title"] = csv_df["meta title"]
csv_df.loc[csv_df["title_count"]=="","title"] = csv_df["meta title"]
csv_df.loc[(csv_df["meta_title_count"]>20) & (csv_df["meta title"]!="(Untitled)"),"title"] = csv_df["meta title"]
csv_df.loc[(csv_df["title_old"]!=""),"title"] = csv_df["title_old"]
csv_df["title"] = csv_df["title"].fillna("(Untitled)")

In [25]:
csv_df["new_url"] = "https://courtformsonline.org/forms/"+csv_df["id"]+".pdf"
csv_df = csv_df.rename(columns={"list":"list_codes","reading grade level":"reading_level",
                                "fields": "standardized_fields","url":"original_url",
                                "fields_old":"original_fields","avg fields per page":"f_per_p",
                                "full_text":"text",
                                "downloaded":"downloaded_on"})

In [26]:
csv_df[["id","title","meta title","group","pages","reading_level","downloaded_on","original_url","original_fields","new_url","standardized_fields","jurisdiction"]]


id  \
0      9fffe321a9fbafdb7964293e8c88e265   
1      9ffd35f8778e21212dd0f319ebb497d2   
2      9ffba05824a302bc69c7fded6244af49   
3      9ff5c8ab7729bc4343ab717c29dba495   
4      9ff5c8ab7729bc4343ab717c29dba495   
...                                 ...   
24714  a12264898b761f4ecdac8977db1116c0   
24715  a078923719fb98f59f9a95de2ad6bfb0   
24716  a074881877409c04b648a9fa2aee6361   
24717  a025934264e01073990c9c9707dea193   
24718  a0201576605f0db775252d8d88fc4d1d   

                                                   title  \
0                                     Writ of Possession   
1      Instructions For Florida Supreme Court Approve...   
2                  GAL - Fee Waiver Application (Family)   
3               Financial Institution Receipt of Letters   
4               Financial Institution Receipt of Letters   
...                                                  ...   
24714                       INSTRUCTIONS FOR FILLING OUT   
24715  Home Detention Screening Criteria (for Home De...   
24716  Microsoft Word - D4F99D126C08CAF6FD5BB80FD7CFF...   
24717  Notice of Confidential Information with Court ...   
24718  CIV-853 |  Order on Motion for Judgment on the...   

                                              meta title  group  pages  \
0                                     Writ of Possession    NaN    2.0   
1      Instructions For Florida Supreme Court Approve...    NaN    9.0   
2                  GAL - Fee Waiver Application (Family)    NaN    3.0   
3                                      STATE OF NEBRASKA    NaN    2.0   
4                                      STATE OF NEBRASKA    NaN    2.0   
...                                                  ...    ...    ...   
24714                       INSTRUCTIONS FOR FILLING OUT    NaN    2.0   
24715  Home Detention Screening Criteria (for Home De...    NaN    4.0   
24716  Microsoft Word - D4F99D126C08CAF6FD5BB80FD7CFF...    NaN    3.0   
24717                                         (Untitled)    NaN    1.0   
24718  CIV-853 Order on Motion for Judgment on the Pl...    NaN    1.0   

      reading_level downloaded_on  \
0                13       2023-03   
1                20       2023-03   
2                10       2023-03   
3                 8       2023-03   
4                 8       2023-03   
...             ...           ...   
24714             7       2023-03   
24715            10       2023-03   
24716            13       2023-03   
24717            11       2023-03   
24718             8       2023-03   

                                            original_url  \
0      https://www.courts.state.hi.us/docs/form/kauai...   
1      https://www.flcourts.gov/content/download/6859...   
2      https://www.mncourts.gov/mncourtsgov/media/Cou...   
3      https://supremecourt.nebraska.gov/sites/defaul...   
4      https://supremecourt.nebraska.gov/sites/defaul...   
...                                                  ...   
24714  https://supremecourt.nebraska.gov/sites/defaul...   
24715  https://www.njcourts.gov/sites/default/files/f...   
24716  https://selfhelp.nvcourts.gov/images/spanish/E...   
24717  https://www.leeclerk.org/home/showpublisheddoc...   
24718  https://public.courts.alaska.gov/web/forms/doc...   

                                         original_fields  \
0      ['clerk__district_court_of_the_above_circuit__...   
1      ['JUDICIAL CIRCUIT', 'COUNTY FLORIDA', 'Case n...   
2      ['petitioner', 'respondent', 'if_a_dependent_l...   
3      ['fullcountystatement222', 'typeofcourt222', '...   
4      ['fullcountystatement222', 'typeofcourt222', '...   
...                                                  ...   
24714  ['c', 'b_enter_your_current_first__middle__and...   
24715  ['cmpltNum', 'res1Addr', 'res6Other', 'res1Pho...   
24716  ['undefined', 'Plaintiff', 'undefined_2', 'de ...   
24717  ['Email address', 'Florida Bar  if applicable'...   
24718  ['courtLocation', 'plaintiff', 'defendant', 'c...   

                       

In [27]:
csv_df.columns

Index(['jurisdiction', 'source', 'group', 'title', 'original_url', 'filename',
       'downloaded_on', 'id', 'index', 'meta title', 'suggested title',
       'description', 'category', 'pages', 'reading_level', 'time to answer',
       'list_codes', 'f_per_p', 'standardized_fields', 'fields_conf',
       'original_fields', 'number of sentences', 'sentences per page',
       'number of passive voice sentences', 'passive sentences',
       'number of all caps words', 'citations', 'total fields',
       'slotin percent', 'gathered percent', 'created percent',
       'third party percent', 'passive voice percent', 'citations per field',
       'citation count', 'all caps percent', 'difficult words',
       'difficult word count', 'difficult word percent',
       'calculation required', 'text', 'title_old', 'title_old_count',
       'title_count', 'meta_title_count', 'new_url'],
      dtype='object')

In [28]:
files_df = csv_df.copy()
files_df = files_df.rename(columns={"avg fields per page":"f_per_p","reading grade level":"reading",
                                "full_text":"text",'downloaded_on':'downloaded',
                                   'original_url':'url', 'standardized_fields':'fields', 'original_fields':'fields_old', 'reading_level':'reading', 
                                    'list_codes':'list'
                                   })
files_df["downloaded_on"] = files_df["downloaded"]
files_df = files_df[['id', 'jurisdiction', 'source', 'title', 'group', 'url', 'filename',
       'downloaded', 'pages', 'fields', 'fields_conf', 'fields_old', 'f_per_p',
       'reading', 'list', 'text', 'downloaded_on']]

In [29]:
for state in csv_df["jurisdiction"].unique():
    tmp_df = csv_df[csv_df["jurisdiction"]==state][["id","title","group","pages","reading_level","downloaded_on","original_url","original_fields","new_url","standardized_fields","jurisdiction"]]
    #display(tmp_df)
    tmp_df.to_csv("docs/data/%s_form_data.csv"%(state), index=False, encoding="utf-8")    

tmp_df = csv_df[["id","title","group","list_codes","pages","f_per_p","reading_level","downloaded_on","original_url","original_fields","new_url","standardized_fields","jurisdiction","text"]]
tmp_df.to_csv("../data/form_data.csv", index=False, encoding="utf-8")       
tmp_df.head()

id  \
0  9fffe321a9fbafdb7964293e8c88e265   
1  9ffd35f8778e21212dd0f319ebb497d2   
2  9ffba05824a302bc69c7fded6244af49   
3  9ff5c8ab7729bc4343ab717c29dba495   
4  9ff5c8ab7729bc4343ab717c29dba495   

                                               title  group  \
0                                 Writ of Possession    NaN   
1  Instructions For Florida Supreme Court Approve...    NaN   
2              GAL - Fee Waiver Application (Family)    NaN   
3           Financial Institution Receipt of Letters    NaN   
4           Financial Institution Receipt of Letters    NaN   

                             list_codes  pages    f_per_p reading_level  \
0                    ['GO-00-00-00-00']    2.0        5.5            13   
1  ['ES-00-00-00-00', 'FA-00-00-00-00']    9.0   7.888889            20   
2                    ['GO-00-00-00-00']    3.0  12.666667            10   
3  ['ES-02-00-00-00', 'ES-00-00-00-00']    2.0        2.5             8   
4  ['ES-02-00-00-00', 'ES-00-00-00-00']    2.0        2.5             8   

  downloaded_on                                       original_url  \
0       2023-03  https://www.courts.state.hi.us/docs/form/kauai...   
1       2023-03  https://www.flcourts.gov/content/download/6859...   
2       2023-03  https://www.mncourts.gov/mncourtsgov/media/Cou...   
3       2023-03  https://supremecourt.nebraska.gov/sites/defaul...   
4       2023-03  https://supremecourt.nebraska.gov/sites/defaul...   

                                     original_fields  \
0  ['clerk__district_court_of_the_above_circuit__...   
1  ['JUDICIAL CIRCUIT', 'COUNTY FLORIDA', 'Case n...   
2  ['petitioner', 'respondent', 'if_a_dependent_l...   
3  ['fullcountystatement222', 'typeofcourt222', '...   
4  ['fullcountystatement222', 'typeofcourt222', '...   

                                             new_url  \
0  https://courtformsonline.org/forms/9fffe321a9f...   
1  https://courtformsonline.org/forms/9ffd35f8778...   
2  https://courtformsonline.org/forms/9ffba05824a...   
3  https://courtformsonline.org/forms/9ff5c8ab772...   
4  https://courtformsonline.org/forms/9ff5c8ab772...   

                                 standardized_fields jurisdiction  \
0  ['clerk_district_court_state', 'duly_authorize...           HI   
1  ['judicia_l_circuit', 'count_florida', '*docke...           FL   
2  ['*petitioners1_name', '*respondents1_name', '...           MN   
3  ['fullcountystatement', 'typeofcourt', 'county...           NE   
4  ['fullcountystatement', 'typeofcourt', 'county...           NE   

                                                text  
0  Writ  of Possession \n\n \n\nin  the District ...  
1  INSTRUCTIONS FOR FLORIDA SUPREME COURT APPROVE...  
2  CONFIDENTIAL \n\nState of Minnesota \nCounty \...  
3  Nebraska State Court Form \nREQUIRED \nCC 16:2...  
4  Nebraska State Court Form \nREQUIRED \nCC 16:2...

In [30]:
all_jurs = [
        ['AL', 'Alabama'], 
        ['AK', 'Alaska'], 
        ['AZ', 'Arizona'], 
        ['AR', 'Arkansas'], 
        ['CA', 'California'], 
        ['CO', 'Colorado'], 
        ['CT', 'Connecticut'], 
        ['DC', 'District of Columbia'], 
        ['DE', 'Delaware'], 
        ['FL', 'Florida'], 
        ['GA', 'Georgia'], 
        ['HI', 'Hawaii'], 
        ['ID', 'Idaho'], 
        ['IL', 'Illinois'], 
        ['IN', 'Indiana'], 
        ['IA', 'Iowa'], 
        ['KS', 'Kansas'], 
        ['KY', 'Kentucky'], 
        ['LA', 'Louisiana'], 
        ['ME', 'Maine'], 
        ['MD', 'Maryland'], 
        ['MA', 'Massachusetts'], 
        ['MI', 'Michigan'], 
        ['MN', 'Minnesota'], 
        ['MS', 'Mississippi'], 
        ['MO', 'Missouri'], 
        ['MT', 'Montana'], 
        ['NE', 'Nebraska'], 
        ['NV', 'Nevada'], 
        ['NH', 'New Hampshire'], 
        ['NJ', 'New Jersey'], 
        ['NM', 'New Mexico'], 
        ['NY', 'New York'], 
        ['NC', 'North Carolina'], 
        ['ND', 'North Dakota'], 
        ['OH', 'Ohio'], 
        ['OK', 'Oklahoma'], 
        ['OR', 'Oregon'], 
        ['PA', 'Pennsylvania'], 
        ['RI', 'Rhode Island'], 
        ['SC', 'South Carolina'], 
        ['SD', 'South Dakota'], 
        ['TN', 'Tennessee'], 
        ['TX', 'Texas'], 
        ['UT', 'Utah'], 
        ['VT', 'Vermont'], 
        ['VA', 'Virginia'], 
        ['WA', 'Washington'], 
        ['WV', 'West Virginia'], 
        ['WI', 'Wisconsin'], 
        ['WY', 'Wyoming']
       ]

default_jur = "MA"

jurs = []
for jur in all_jurs:
    if jur[0] in forms_df["jurisdiction"].unique():
        jurs.append(jur)
        
print("length",len(jurs))

length 46


In [31]:
import requests
import json

def vectorize(text):
    governor(0,50,66.66,0)
    try:
        # This is your real token.
        token = ""
        headers = { "Authorization": "Bearer " + token, "Content-Type":"application/json" }
        # Find Embeddings
        body = {
          "text": text
        }
        r = requests.post('https://tools.suffolklitlab.org/vectorize/', headers=headers, data=json.dumps(body))
        output_1 = r.json()

        return output_1["embeddings"]
    except:
        print("ERROR!!!")
        return []

In [32]:
vectorize("text goes here")

[0.08158453646136106,
 0.007466353416808095,
 0.016883352096717128,
 0.004566527569989328,
 0.050255235812826975,
 -0.04424023811869246,
 0.087127284055433,
 0.032124483112883025,
 -0.07219764455542918,
 0.04688190383876885,
 0.18424665477074786,
 0.06636156767070442,
 -0.13134308988673912,
 0.05714450579038107,
 0.06494501723881306,
 -0.00585148165307303,
 0.11972666713514618,
 0.024047732724976303,
 -0.002279476965811508,
 0.04741670626822111,
 -0.039431142566836844,
 -0.049916217274367514,
 0.01114373181298966,
 -0.0885908938000656,
 -0.09992365830760278,
 -0.03596910775339061,
 -0.024571447299505052,
 -0.08243996632232739,
 -0.018387797835605745,
 0.058310202168273845,
 -0.027437020314078454,
 -0.058864572348674135,
 -0.029197199149973867,
 -0.08410548817781312,
 -0.04098165311250829,
 -0.06260622290869856,
 -0.0609336605312902,
 -0.03625142816933378,
 0.12316732893561295,
 0.08256255650899155,
 -0.05228367336291345,
 0.02452639795261491,
 -0.04484499445186336,
 -0.0013908705794940

In [33]:
from sklearn.decomposition import PCA
import re
import json

In [34]:
%%time
test_vec = tmp_df.copy()
#test_vec["vec"] = test_vec["text"].apply(vectorize)

CPU times: user 8.58 ms, sys: 263 µs, total: 8.84 ms
Wall time: 8.53 ms


In [ ]:
%%time
test_vec["vec"] = "[]"

#test_vec = test_vec[:2]
#display(test_vec)

i = 0
p_1 = round(len(test_vec)/100)
print("Starting...")
for index,row in test_vec.iterrows():
    if (row["vec"]=="[]") & (len(str(row["text"]))>5):
        try:
            embedding = vectorize(row["text"])
            test_vec.loc[index,"vec"] = str(embedding)
        except:
            print("ERROR!!!")
    i+=1
    if i%p_1==0:
        print("{}) {}% done...".format(i,i/p_1))
        governor(0,50,66.66,1)
    else:
        governor(0,50,66.66,0)
print("DONE\n\n")

Starting...
    Slowing down...
    Slowing down...
ERROR!!!
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
247) 1.0% done...

 Usage: CPU 0.0% & Memory 60.3%

    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
494) 2.0% done...

 Usage: CPU 5.6% & Memory 63.0%

    Slowing down...
741) 3.0% done...

 Usage: CPU 6.9% & Memory 62.9%

    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
988) 4.0% done...

 Usage: CPU 7.3% & Memory 63.3%

    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
1235) 5.0% done...

 Usage: CPU 5.4% & Memory 63.2%

    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
1482) 6.0% done...

 Usage: CPU 8.9% & Memory 63.8%

    S

    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
6175) 25.0% done...

 Usage: CPU 6.6% & Memory 63.7%

    Slowing down...
    Slowing down...
    Sl

14079) 57.0% done...

 Usage: CPU 4.1% & Memory 65.7%

    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    Slowing down...
    S

In [ ]:
vec_df_low =test_vec["vec"].to_list()
pca2 = PCA(n_components=100)
pca2.fit(vec_df_low)

In [ ]:
dump(pca2,"../data/pca.joblib")

In [732]:
def pca_form(text):
    return list(pca2.transform([vectorize(text)])[0])

In [734]:
#pca_form("test")

In [ ]:
vec_df_low = pca2.transform(vec_df_low)
test_vec["PCA"] = list(vec_df_low)
test_vec

In [ ]:
test_vec.columns

In [ ]:
test_vec.loc[pd.isnull(test_vec["list_codes"]),"list_codes"] = "[]"
test_vec.loc[test_vec["list_codes"]=="{'status': 400, 'message': '`text` must be greater than 5 and less than 5,000 characters long.'}","list_codes"] = "[]"
#test_vec.loc[pd.isnull(test_vec["reading_level"]),"reading_level"] = None

In [ ]:
#test_vec["group"]#.unique()

In [ ]:
formsinfo = "var FormsInfo = [\n\t"
i = 1
for index,row in test_vec.iterrows():
    title = row["title"] + " (%s)"%row["jurisdiction"]
    title = re.sub('\s+',' ',title)
    text = row["text"]
    if pd.isnull(text):
        text = ""
    text = title +" "+ text
    reading = row["reading_level"]
    if pd.isnull(reading):
        reading = "null"
    pages = row["pages"]
    if pd.isnull(pages):
        pages = "null"
    f_per_p = row["f_per_p"]
    if pd.isnull(f_per_p):
        f_per_p = "null"
    fields = row["standardized_fields"]
    if pd.isnull(fields):
        fields = []
    formsinfo += "{"
    formsinfo += """
\t"fid":"%s",
\t"jur":"%s",
\t"name":%s,
\t"reading":%s,
\t"pages":%s,
\t"f_per_p":%s,
\t"label":%s,
\t"list":%s,
\t"fields":%s,
\t"text":%s,
\t"vec":%s
"""%(row["id"],row["jurisdiction"],json.dumps(title),reading,pages,f_per_p,json.dumps(row["group"]),row["list_codes"],fields,json.dumps(text),np.array2string(row["PCA"],separator=','))
    formsinfo += "\t}"
    if i < len(test_vec):
        formsinfo += ","
    else:
        formsinfo += "\n"
    i+=1

formsinfo = re.sub("\n|\t","",formsinfo)
    
formsinfo += "]\n"

In [ ]:
text_file = open("docs/js/formsinfo.js", "w")
text_file.write(formsinfo)
text_file.close()

In [71]:
def header(title,description,path="./",wide=0):
    
    if wide==1:
        pclass = "content_wide"
    else:
        pclass = "content"
    
    html = """<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Transitional//EN" "http://www.w3.org/TR/xhtml1/DTD/xhtml1-transitional.dtd">
<HTML xmlns="http://www.w3.org/1999/xhtml"
      xmlns:og="http://ogp.me/ns#"
      xmlns:fb="http://www.facebook.com/2008/fbml">
<HEAD>
    <title>%s</title>
    <!-- Global site tag (gtag.js) - Google Analytics -->
    <script async src="https://www.googletagmanager.com/gtag/js?id=UA-108858221-1"></script>
    <script>
      window.dataLayer = window.dataLayer || [];
      function gtag(){dataLayer.push(arguments);}
      gtag('js', new Date());

      gtag('config', 'UA-108858221-1');
    </script>
    <meta http-equiv="Content-type" content="text/html;charset=UTF-8"/>
    <meta name="viewport" content="width=device-width, initial-scale=1.0, maximum-scale=1.0, user-scalable=0" />
    <meta name="apple-mobile-web-app-capable" content="no" />
    <link rel="apple-touch-icon" href="%simages/icon_300.png"/>
    <meta property="og:type" content="website"/>
    <meta property="og:title" content="%s"/>
    <meta property="og:description" content="%s"/>
    <meta property="og:image" content="%simages/bigdata.png"/>

    <meta name="twitter:card" content="summary_large_image">
    <meta name="twitter:site" content="@SuffolkLITLab">
    <meta name="twitter:creator" content="@SuffolkLITLab">
    <meta name="twitter:title" content="%s">
    <meta name="twitter:description" content="%s">
    <meta name="twitter:image" content="http://www.davidcolarusso.com/images/bigdata.png"/>

    <meta http-equiv="X-UA-Compatible" content="IE=edge" />
    <link rel="shortcut icon" type="image/x-icon" href="/favicon.ico">
    <link rel="apple-touch-icon" href="%simages/icon.png"/>
    <link rel="stylesheet" href="https://code.jquery.com/ui/1.11.1/themes/smoothness/jquery-ui.css">
    <link rel="stylesheet" type="text/css" href="%scss/style.css?v=%s">
    <script src="https://code.jquery.com/jquery-1.11.1.min.js"></script>
    <script src="https://code.jquery.com/jquery-1.10.2.js"></script>
    <script src="https://code.jquery.com/ui/1.11.1/jquery-ui.js"></script>

</HEAD>
<BODY BGCOLOR="#ffffff" BACKGROUND="" MARGINWIDTH="0" MARGINHEIGHT="0">
<div style="box-sizing: border-box;width:100%%;background:#f6d91b;color:black;padding:15px;text-align:center;">
<b>This tool is in beta.</b> <b>CONTENT IS SUBJECT TO CHANGE!</b></div>
<div class="%s">

    <div id="icon" style="background-size: 100px 100px;background-image: url('%simages/seal.jpg');"><a href="%s" alt="home"><img src="%simages/space.gif" width="100px" height="100px;" border="0" alt="LIT Logo"/></a></div>
    <h1 style="text-align:center;">
        The Legal Innovation & Technology Lab's Form Explorer <sup><font size=+1>Beta</font></sup>
        <center style="margin-top:5px;">
          <span class="subtitle">@ Suffolk Law School&nbsp;<font style="font-weight:normal">Last updated %s</font></span>
        </center>
    </h1>
"""%(title,path,title,description,path,title,description,path,path,today,pclass,path,path,path,today)
    return html
    
def footer(path="./"):
    html = """

<div class="footer">
    <a href="/" alt="home"><img src="%simages/blue_logo.png" width="50px" align="left" border="0" alt="LIT Logo"/></a>
<font size=-1><a href="mailto:litlab@suffolk.edu">Email</a> | <a href="https://github.com/SuffolkLITLab" target="_blank">GitHub</a> | <a href="/terms">Terms &amp; Privacy</a> | <a href="/credits">Credits</a></font>
</div>

</BODY>
</HTML>
"""%(path)
    
    return html

# Home page

In [72]:
def home():
    html = """
    <div class="menu_bar">
        <p style="text-align:center;">
      <a href="https://suffolklitlab.org/" class="menu">&nbsp;LIT Lab Home&nbsp;</a>&nbsp;<font style="color:#888;">|</font>&nbsp;
      <a href="." class="menu" style="color:black;">&nbsp;About&nbsp;The&nbsp;Explorer&nbsp;</a>&nbsp;<font style="color:#888;">|</font>&nbsp;
      <a href="compare" class="menu">Find&nbsp;&amp;&nbsp;Compare&nbsp;</a><font style="color:#888;">|</font>&nbsp;

      &nbsp;&nbsp;<span style="font-family: sans-serif;font-size: 12px;text-transform: uppercase;">Explore:</span>&nbsp;&nbsp;
      <a href="list/" class="menu">&nbsp;Lists&nbsp;</a>
      <!--<a href="sim/" class="menu">&nbsp;Similar Forms&nbsp;</a>
      <a href="flow/" class="menu">&nbsp;Flows&nbsp;</a>-->
      
        </p>
    </div>

  <div class="content"><h2><a name="title" href="#title" class="anchor"></a>What is the Form Explorer?</h2>

    <div style="float:left;width:100%%">
      <div class="r_img_embed" style="max-width:500px;">
        <img src="images//bigdata.png" alt="Image of the character Data as a giant standing next to the Supreme Court" width="100%%"/>
        <div class="caption">Big Data &amp; the Law, h/t <a href="https://flic.kr/p/7YZubW" target="_blank">Tim Sackton</a> &amp; <a href="https://medium.com/@wtrsld/big-data-made-me-do-it-5bfc3f46871c" target="_blank">Josh Lee</a></div>
      </div>
      <p>
        We're collecting existing pdf forms from multiple jurisdictions and making it possible for folks (e.g., courts and non-profits) to turn them into beautiful webapps with ease. Eventually, you will be able to go from form to prototype webapp in a few clicks. As time goes by, we'll grow the number of jurisdictions and improve our tools' performance. They'll never do all of the work, but they help plot a course for what otherwise might seem an "impossible" task. They'll help make things concrete, allowing for stakeholders and developers to edit their way to a production-ready solution built on suggestions rooted in years of form building experience.
      </p>
      <p>
        For many, interaction with a court involves completing a "form," and often, this means filling out either a paper form or pdf facsimile. Occasionally, the latter can be found online and come with embedded fillable fields. Most of the time, however, this just means one can type in the fields before printing the form. The infrastructure that has grown up around court forms too often focus on delivering either a physical form or pictures of such to the court. Very rare is the form that can easily be filled out on a phone absent specialty software, and even more rare is the form that helps guide users through the process. 
        There are exceptions, like the forms found at <a href="https://lawhelpinteractive.org/" target="_blank">LawHelp Interactive</a> or the growing constellation of <a href="https://www.a2jauthor.org/" target="_blank">A2J Author</a>-driven forms found across multiple jurisdictions. Yet, the majority of court processes linked to forms have failed to keep pace with our technical ability to offer context-aware mobile friendly fully-electronic interactions. This Form Explorer is part of a broader open-source effort—<a href="https://suffolklitlab.org/docassemble-AssemblyLine-documentation/" target="_blank">the Document Assembly Line</a>—aimed at changing this. To learn more about how we got started, check out <a href="https://papers.ssrn.com/sol3/papers.cfm?abstract_id=3911381" target="_blank">Digital Curb Cuts: Towards an Inclusive Open Forms Ecosystem</a>, a law review article describing the project's genesis.
      </p>
      <p>
        On this site you can explore the connections between forms and get a feel for populations of existing forms, allowing you to strategize how best to redesign or translate flat forms into vibrant interactive web apps. 
      </p>
      <h2><a name="data" href="#data" class="anchor"></a>Our Data</h2>
      <p>
        Currently, we've downloaded and parsed %s forms from %s jurisdictions. Use the menu above to explore, or download summary data here: <a href="https://courtformsonline.org/forms/form_data.csv" target="_blank">form_data.csv</a> And please remember this is a work in progress. So, everything here is subject to change including things like fields we find and how we calculate readability. 
      </p>
      <h2><a name="data" href="#tools" class="anchor"></a>Our Tools</h2>
      <p>
        To mine data from these forms we created an open source python package—FormFyxer. You can find it and its documentaion on GitHub here: <a href="https://github.com/SuffolkLITLab/FormFyxer" target="_blank">https://github.com/SuffolkLITLab/FormFyxer</a>
      </p>
    </div>"""%(len(tmp_df),len(tmp_df["jurisdiction"].unique()))   
    return html

In [73]:
html = header("About the Form Explorer?","""We're collecting existing pdf forms from multiple jurisdictions and making it possible for folks (e.g., courts and non-profits) to turn them into beautiful webapps with ease. Eventually, you will be able to go from form to prototype webapp in a few clicks. As time goes by, we'll grow the number of jurisdictions and improve our tools' performance. They'll never do all of the work, but they help plot a course for what otherwise might seem an "impossible" task. They'll help make things concrete, allowing for stakeholders and developers to edit their way to a production-ready solution built on suggestions rooted in years of form building experience.""")+home()+footer()
text_file = open("docs/index.html", "w")
text_file.write(html)
text_file.close()

# redirects

In [74]:
def redirects(jur):
    html = """<html>
<head>
<META http-equiv="CACHE-CONTROL" CONTENT="NO-CACHE">
<meta http-equiv="refresh" content="0; url=%s" />
</head>
</html>
"""%jur
    return html

In [75]:
html = redirects(default_jur)

#text_file = open("docs/sim/index.html", "w")
#text_file.write(html)
#text_file.close()

#text_file = open("docs/flow/index.html", "w")
#text_file.write(html)
#text_file.close()

#text_file = open("docs/list/index.html", "w")
#text_file.write(html)
#text_file.close()

# List VIew

In [76]:
def listview(jur,path="./"):
    
    pages = files_df[(files_df["jurisdiction"]==jur[0])]["pages"].mean()
    f_per_p = files_df[(files_df["jurisdiction"]==jur[0])]["f_per_p"].mean()
    fields = files_df[(files_df["jurisdiction"]==jur[0])]["f_per_p"].mean()*files_df[(files_df["jurisdiction"]==jur[0])]["pages"].mean()
    reading = files_df[(files_df["jurisdiction"]==jur[0])]["reading"].median()
    forms= len(files_df[(files_df["jurisdiction"]==jur[0])])
    
    html = """
    <div class="menu_bar">
        <p style="text-align:center;">
      <a href="https://suffolklitlab.org/" class="menu">&nbsp;LIT Lab Home&nbsp;</a>&nbsp;<font style="color:#888;">|</font>&nbsp;
      <a href="../../" class="menu">&nbsp;About&nbsp;The&nbsp;Explorer&nbsp;</a>&nbsp;<font style="color:#888;">|</font>&nbsp;
      <a href="../../compare" class="menu">Find&nbsp;&amp;&nbsp;Compare&nbsp;</a><font style="color:#888;">|</font>&nbsp;

      &nbsp;&nbsp;<span style="font-family: sans-serif;font-size: 12px;text-transform: uppercase;">Explore:</span>&nbsp;&nbsp; <select style="width:100px;" onChange="window.location.href='../'+this.value">"""
    
    for item in jurs: 
        if item[0]==jur[0]:
            selected = "SELECTED"
        else:
            selected = ""
        html += "<option value=\"%s\" %s>%s</option>"%(item[0],selected,item[1])
        
    html += """
      </select>&nbsp;&nbsp;
      <a href="../../list/%s" class="menu" style="color:black;">&nbsp;Lists&nbsp;</a>
      <!--<a href="../../sim/%s" class="menu">&nbsp;Similar Forms&nbsp;</a>
      <a href="../../flow/%s" class="menu">&nbsp;Flows&nbsp;</a>-->
        </p>
    </div>
"""%(jur[0],jur[0],jur[0])
    
    html += """
    <div class="content">
    <h2><a name="title" href="#title" class="anchor"></a>List of %s Court Forms</h2>
    
    <div class="sidebar">
        <h2>Search %s Forms</h2>
        <table cellpadding="0px"><tr><td width="100%%">
        <input id="q" style="width:100%%">
        </td><td width="1%%">&nbsp;&nbsp;&nbsp;</td><td width="1%%">
        <input type="button" value="Search" onClick="open_search();">
        </td></tr></table>
        <script>
            sort_links();

            function open_search(){
                alert('Coming Soon!');
            }
            function open_search_(){
                window.open('https://www.google.com/search?q='+$('#q').val()+'+site:suffolklitlab.org/form-explorer/form/%s')
            }
            $("#q").on('keyup', function (e) {
                if (e.key === 'Enter' || e.keyCode === 13) {
                    open_search()
                }
            });
        </script>
    </div>

    <p>
    Below you will find %s unique forms. The average form is %.0f pages long, with %.0f fields per page. The median form is written at a %.2f-grade reading level.
    </p>
    
    <p>Download a .csv file with meta data on all %s forms, including source urls, field names, reading levels, et al.: 
    <a href="../../data/%s_form_data.csv" target="_blank">%s_form_data.csv</a>
    </p>
    

    <div id="court_grouping" style="display:none;width:100;">
    
    <p><i>Links are grouped by categories found on the court's website.</i></p>
    
    """%(jur[1],jur[1],jur[0],forms,pages,fields,reading,forms,jur[0],jur[0])

    #for cat in files_df[files_df["jurisdiction"]==jur[0]]["group"].unique():
    #    html += """
    #    <h3><a name="%s" href="#%s" class="anchor"></a>%s</h3>
    #    <ul>"""%(removeSpecial(cat),removeSpecial(cat),cat)

    #    for index,row in files_df[(files_df["jurisdiction"]==jur[0]) & (files_df["group"]==cat)].iterrows():
            #print(row[1][0])
    #        html += """<li><a href="../../form/%s/%s.html">%s</a></li>"""%(jur[0],row["id"],row["title"])
            
    #    html += "</ul><p style=\"text-align:center\"><a href=\"#title\">go to top</a></p>"
        
    html+="""</div>
    
    <div id="LIST_grouping" style="width:100;">
    
    <p><i>Links are grouped by categories from the <a href="https://taxonomy.legal/" target="_blank" class="exlink">Legal Issue Taxonomy (LIST)</a>. 
    Note: the following grouping was done by machine. 
    """

    list_group = files_df[(files_df["list"]=="[]") & (files_df["jurisdiction"]==jur[0])]
    if len(list_group)>0:
        html+="""
        Forms without an identifed group can befound under the <a href="#unclassifed">Unclassified</a> header.</i></p>
        """
    
    lookfor = [
                ["BE","Public Benefits"],
                ["WO","Work and Employment Law"],
                ["ES","Estates, Wills, and Gaurdianships"],
                ["CR","Crime and Prisons"],
                ["FA","Family"],
                ["TO","Accidents and Torts"],
                ["TR","Trafic and Cars"],
                ["HE","Health"],
                ["MO","Money, Debt, and Consumer Issues"],
                ["HO","Housing"],
                ["VE","Veterans and Military"],
                ["IM","Immigration"],
                ["DI","Disaster Relief"],
                ["RI","Civil and Human Rights"],
                ["EN","Environmental Justice"],
                ["NA","Native American Issues and Tribal Law"],
                ["ED","Education"],
                ["BU","Small Business and IP"],
                ["GO","Government Services"],
                ["CO","Courts and Lawyers"],
              ]
    
    for item in lookfor:
        list_group = files_df[(files_df["list"].str.contains(item[0])) & (files_df["jurisdiction"]==jur[0]) & (files_df["list"]!="[]")]
        if len(list_group)>0:
            html+="<h3><a name=\"%s\" href=\"#%s\" class=\"anchor\"></a>%s</h3><ul>"%(item[1],item[1],item[1])
            for index,row in list_group.iterrows():
                html += """<li><a href="../../form/%s/%s.html">%s</a></li>"""%(jur[0],row["id"],row["title"])
            html+="</ul>"
            html+="""<p style="text-align:center"><a href="#title">go to top</a></p>"""
        #else:
        #    html+="<h3 style=\"color:gray\">%s</h3>"%item[1]
        
        
    list_group = files_df[(files_df["list"]=="[]") & (files_df["jurisdiction"]==jur[0])]
    if len(list_group)>0:
        html+="<h3><a name=\"unclassifed\" href=\"#unclassifed\" class=\"anchor\"></a>Unclassified</h3><ul>"
        for index,row in list_group.iterrows():
            html += """<li><a href="../../form/%s/%s.html">%s</a></li>"""%(jur[0],row["id"],row["title"])
        html+="</ul>"
        html+="""<p style="text-align:center"><a href="#title">go to top</a></p>"""
        
    html+="""
    </div>
    
    <div id="most_used" style="display:none;width:100;">
    
    <p><i>Links are orderd by most used.</i></p>
    
    <p style="background:#fcf19d">
        <i>
            <b>Under Construction:</b> With historical form data we could provde insights on how frequently forms are used.
            If you work with the court and can help provide historic form data, <a href="mailto:litlab@suffolk.edu">let us know</a>.
        </i>
    </p>
    
    </div>
    """
        
    #for field in included_fields:
    #    print("\t"+field)
    #    html += """<li><a href="fields/%s.html">%s</a></li>"""%(field,field)
        
    html+="</div>"

    return html

In [77]:
files_df['f_per_p'] = files_df['f_per_p'].fillna(0)

In [78]:
#files_df[files_df['f_per_p'].str.contains("brevity")]

In [79]:
files_df[files_df['f_per_p']=="['throughout_word_used_brevity', 'page_field__1', 'page_field__2', 'page_field__3', 'page_field__4', 'page_field__5', 'page_field__6', 'page_field__7', 'page_field__8', 'page_field__9', 'page_field__10', 'page_field__11', 'page_field__12', 'page_field__13', 'page_field__14', 'page_field__15', 'page_field__16', 'page_field__17', 'page_field__18', 'page_field__19', 'page_field__20', 'page_field__21', 'page_field__22', 'page_field__23', 'page_field__24', 'page_field__25', 'page_field__26', 'page_field__27', 'page_field__28', 'page_field__29', 'montana_university_bozeman_mt']"]

id jurisdiction source  \
9087  for Owners of Pets & Companion or Service Animals          NaN    NaN   

           title  group  url filename downloaded  pages  \
9087  (Untitled)    NaN  NaN      NaN    2023-03   15.0   

                                                 fields  \
9087  [0.55, 0.31, 0.36, 0.36, 0.36, 0.36, 0.36, 0.3...   

                                            fields_conf fields_old  \
9087  ['throughout_this_montguide_the_word__pet__wil...        159   

                                                f_per_p      reading  \
9087  ['throughout_word_used_brevity', 'page_field__...  [18.0, 3.7]   

                                                   list text downloaded_on  
9087  {'status': 400, 'message': '`text` must be gre...  NaN       2023-03

In [787]:
test = files_df.copy()
test = test.drop([0, 9087])
#test.loc[9087]

In [80]:
files_df = files_df.drop([0, 9087])

In [81]:
#files_df["f_per_p"].mean()

In [82]:
files_df["f_per_p"] = pd.to_numeric(files_df["f_per_p"])#.mean()

In [83]:
for jur in jurs:    
    print(jur)
    path = "../../"
    
    if not os.path.exists("docs/list/%s"%(jur[0])):
        os.makedirs("docs/list/%s"%(jur[0]))
    #else:
    #    shutil.rmtree("docs/list/%s"%(jur[0]))
    #    os.makedirs("docs/list/%s"%(jur[0]))
        
    html = header("%s Court Forms"%jur[1],"""We're collecting existing pdf forms from multiple jurisdictions and making it possible for folks (e.g., courts and non-profits) to turn them into beautiful webapps with ease. Eventually, you will be able to go from form to prototype webapp in a few clicks. As time goes by, we'll grow the number of jurisdictions and improve our tools' performance. They'll never do all of the work, but they help plot a course for what otherwise might seem an "impossible" task. They'll help make things concrete, allowing for stakeholders and developers to edit their way to a production-ready solution built on suggestions rooted in years of form building experience.""",path,wide=0)+listview(jur,path)+footer(path)
    text_file = open("docs/list/%s/index.html"%(jur[0]), "w", encoding="utf-8")
    text_file.write(html)
    text_file.close()

['AL', 'Alabama']
['AK', 'Alaska']
['AR', 'Arkansas']
['CA', 'California']
['CO', 'Colorado']
['CT', 'Connecticut']
['DC', 'District of Columbia']
['DE', 'Delaware']
['FL', 'Florida']
['GA', 'Georgia']
['HI', 'Hawaii']
['ID', 'Idaho']
['IL', 'Illinois']
['IA', 'Iowa']
['KS', 'Kansas']
['KY', 'Kentucky']
['LA', 'Louisiana']
['ME', 'Maine']
['MD', 'Maryland']
['MA', 'Massachusetts']
['MI', 'Michigan']
['MN', 'Minnesota']
['MS', 'Mississippi']
['MT', 'Montana']
['NE', 'Nebraska']
['NV', 'Nevada']
['NJ', 'New Jersey']
['NY', 'New York']
['NC', 'North Carolina']
['ND', 'North Dakota']
['OH', 'Ohio']
['OK', 'Oklahoma']
['OR', 'Oregon']
['PA', 'Pennsylvania']
['RI', 'Rhode Island']
['SC', 'South Carolina']
['SD', 'South Dakota']
['TN', 'Tennessee']
['TX', 'Texas']
['UT', 'Utah']
['VT', 'Vermont']
['VA', 'Virginia']
['WA', 'Washington']
['WV', 'West Virginia']
['WI', 'Wisconsin']
['WY', 'Wyoming']


# Create form pages

In [84]:
def formview(jur,path="./"):
    html = """
    <div class="menu_bar">
        <p style="text-align:center;">
      <a href="https://suffolklitlab.org/" class="menu">&nbsp;LIT Lab Home&nbsp;</a>&nbsp;<font style="color:#888;">|</font>&nbsp;
      <a href="../../" class="menu">&nbsp;About&nbsp;The&nbsp;Explorer&nbsp;</a>&nbsp;<font style="color:#888;">|</font>&nbsp;
      <a href="../../compare" class="menu">Find&nbsp;&amp;&nbsp;Compare&nbsp;</a><font style="color:#888;">|</font>&nbsp;
      &nbsp;&nbsp;<span style="font-family: sans-serif;font-size: 12px;text-transform: uppercase;">Explore: """
    
    for item in jurs: 
        if item[0]==jur[0]:
            this_state = item[1]
            html += "%s"%this_state

    html += """
      </span>&nbsp;&nbsp;
      <a href="../../list/%s" class="menu">&nbsp;Lists&nbsp;</a>
      <!--<a href="../../sim/%s" class="menu">&nbsp;Similar Forms&nbsp;</a>
      <a href="../../flow/%s" class="menu">&nbsp;Flows&nbsp;</a>-->
        </p>
    </div>

"""%(jur[0],jur[0],jur[0])
    
    if jur[0]!="CA":
        linkurl = "https://courtformsonline.org/forms/%s.pdf"%row["id"]
        iframelink = linkurl
    else:
        linkurl = "javascript:alert('Califonia machine-processed forms are not yet available.')"
        iframelink = "https://courtformsonline.org/forms/%s.pdf"%row["id"]
        
    html += """
  <div class="content_wide" style="padding-left:0px;">
    <div class="pdf">
      <iframe src="%s" width="100%%" height="1100px;"></iframe>
      <div id="form_text" style="display:none;overflow:hidden;padding:20px;">Here is the text we could read: 
      <pre>%s</pre></div>
    </div>
    <div class="pdfinfo">
      <h1><a name="title" href="#title" class="anchor"></a>%s</h1>
      <p>
        This info page is part of the LIT Lab's <i>Form Explorer</i> project. It is not associated with the %s state courts. 
        To learn more about the project, check out our <a href="../../">about page</a>.
      </p>
      <p>
        <b>Downloads:</b> You can download both the <a href="%s" target="_blank" class="exlink">original form</a> (last checked %s) 
        and the <a href="%s">machine-processed form</a> with normalized data fields.
      </p>

        <hr style="border: 1px solid #fff;border-bottom: 1px solid #555;">
      <h3><a name="about_form" href="#about_form" class="anchor"></a>About This Form:</h3>
      <ul>"""%(iframelink,row["text"],row["title"],this_state,row["url"],row["downloaded"],linkurl)
    
    html += """
        <li>Sourced from <a href="http://%s" target="_blank" class="exlink">%s</a> (%s)</li>
        <li>Page(s): %s </li>
        <li>Fields(s): %s </li>
        <li>Average fields per page: %s</li>
        <li>Reading Level: Grade %s</li>
        <li><a href="https://taxonomy.legal/" target="_blank" class="exlink">LIST</a> Grouping(s): 
    """%(row["source"],row["source"],row["downloaded"],clean_n(row["pages"]),clean_n(row["pages"]*row["f_per_p"]),clean_n(row["f_per_p"]),clean_n(row["reading"]))
    
    if pd.notnull(row["list"]):
        j= 0
        nsmi = eval(row["list"])
        if len(nsmi)>0:
            for f in nsmi:
                #html += "<a href=\"https://taxonomy.legal/term/%s\" target=\"_blank\">%s</a>"%(f,f)
                html += "%s"%(f)
                if j==len(nsmi)-1:
                    html+=". "
                else:
                    html+=", "
                j+=1    
        else:
            html+="Unknown"
    else:
            html+="Unknown"
            nsmi = []
        
    html += """        
        </li>
      </ul>
      <p>
      <i>Use our <a href="https://ratemypdf.com" target="_blank">Rate My PDF</a> tool to learn more.</i> 
      Go beyond the above insights and learn more about this or any pdf form at 
      <a href="https://ratemypdf.com" target="_blank">RateMyPDF.com</a>, includes: counts of difficult words used, 
      passive voice decetion, and suggestions for how to make the form more usable.
      </p>
      <hr style="border: 1px solid #fff;border-bottom: 1px solid #555;">
      <h3><a name="fields" href="#fields" class="anchor"></a>Identified Data Fields:</h3>
      <p>We have done our best to automaticly identify and name form fields according to our <a href="https://suffolklitlab.org/docassemble-AssemblyLine-documentation/docs/label_variables/">naming conventions</a>. 
      When possible, we've used names tied to our question library. See e.g., <a href="https://suffolklitlab.org/docassemble-AssemblyLine-documentation/docs/question_library/names">user1_name</a>.
      If we think we've found a match to a question in our library, it is highlighted in green. Novel names are auto generated. So, you will probably need to edit some of them if you're trying to stick to the convention.
      </p>
      
      <div style="float:left;width:100%%;margin-bottom:25px;">
          <div class="tab" style="border: 1px solid #fff;border-bottom: 1px solid #555;width:15px;padding:10px 0px;">&nbsp;</div>
          <div class="tab" id="tab1" style="border-bottom: 1px solid #fff;" >
              <a href="javascript:void('');" onClick="tab_focus('orig_fields');" class="menu" id="atab1" style="color:black;">Original Order</a>
          </div>
          <div class="tab" style="border: 1px solid #fff;border-bottom: 1px solid #555;width:15px;padding:10px 0px;">&nbsp;</div>
          <div class="tab" id="tab2">
              <a href="javascript:void('');" onClick="tab_focus('sug_screens');" class="menu" id="atab2">Suggested Screens</a>
          </div>
          <div class="tab" style="border: 1px solid #fff;border-bottom: 1px solid #555;">
              &nbsp;
          </div>
      </div>
      <script>
          function tab_focus(tab){
              if (tab=="orig_fields") {
                  $('#sug_screens').hide();
                  $('#orig_fields').show();
                  $('#tab1').css('border-bottom-color', '#fff;');
                  $('#tab2').css('border-bottom-color', '#555;');
                  $('#atab1').css('color', 'black');
                  $('#atab2').css('color', '#529ecc');
              } else {
                  $('#orig_fields').hide();
                  $('#sug_screens').show();
                  $('#tab1').css('border-bottom-color', '#555;');
                  $('#tab2').css('border-bottom-color', '#fff;');
                  $('#atab1').css('color', '#529ecc');
                  $('#atab2').css('color', 'black');
              }
          }
      </script>
      
      """%()
    
    
    html+="<div id=\"orig_fields\" style=\"padding-left:15px;\"><p>Here are the fields we could identify.</p>"
    html+="<div style=\"max-height:550px;overflow-y: auto;padding-bottom:25px;\"><ul>"
        
    if not pd.isnull(row["fields"]):
        if len(eval(row["fields"]))==0:
            html+="<li>No fields found</li>"
        else:        
            j = 0
            for f in eval(row["fields"]):
                html += "<li>"
                if re.search('^\*',f):
                    f = re.sub("^\*","",f)
                    f_link = re.sub("__\d+$","",f)
                    #v = re.search('^(\w*)',f).groups()[0]
                    #f = re.sub("\|","</code></a>",f)
                    html +="<code style=\"background:#a2e874\"><a href=\"../../list/%s/fields/%s.html\">%s</a></code> was <i>%s</i> (%.2f conf)<!--100%% completed. <a href=\"\">Learn more about distribution of answers.</a>--></li>"%(jur[0],f_link,f,eval(row["fields_old"])[j],eval(row["fields_conf"])[j])   
                else: 
                    #v = re.search('^(\w*)',f).groups()[0]
                    #f = re.sub("\|","</code>",f)
                    html +="<code>%s</code> was <i>%s</i> (%.2f conf)<!--100%% completed. <a href=\"\">Learn more about distribution of answers.</a>--></li>"%(f,eval(row["fields_old"])[j],eval(row["fields_conf"])[j])
                j+=1    
                
    else:
        html+="<li>No fields found</li>"

    html+="</ul></div></div>"
        
    html+="<div id=\"sug_screens\" style=\"display:none;padding-left:15px;\"><p>We've done our best to group similar variables togther to avoid overwhelming the user.</p>"
    html+="<div style=\"max-height:550px;overflow-y: auto;padding-bottom:25px;\">"

    if not pd.isnull(row["fields"]):
        if len(eval(row["fields"]))==0:
            html+="<ul><li>No fields found</li>"
        else:       
            screens = lit.cluster_screens(eval(row["fields"]),damping=0.5)
            i = 0
            for screen in screens:
                html+="<p>Suggested Screen %s:</p><ul>"%i
                j = 0
                for f in screens[screen]:
                    html += "<li>"
                    if re.search('^\*',f):
                        f = re.sub("^\*","",f)
                        f_link = re.sub("__\d+$","",f)
                        #v = re.search('^(\w*)',f).groups()[0]
                        #f = re.sub("\|","</code></a>",f)
                        html +="<code style=\"background:#a2e874\"><a href=\"../../list/%s/fields/%s.html\">%s</a></code></li>"%(jur[0],f_link,f)   
                    else: 
                        #v = re.search('^(\w*)',f).groups()[0]
                        #f = re.sub("\|","</code>",f)
                        html +="<code>%s</code></li>"%(f)
                    j+=1    
                i+=1
                html+="</ul>"
    else:
        html+="<li>No fields found</li>"    

    html+="</div></div>"

        
    html += """
      
      <hr style="border: 1px solid #fff;border-bottom: 1px solid #555;">
      <h3><a name="weaver" href="#weaver" class="anchor"></a>Create an Interactive Version of this Form:</h3>
      <p>
      The Weaver creates a draft guided interview from a template form, like the one provided here. You can use the link below to open this form in the Weaver.
      To learn more, read <a href="https://suffolklitlab.org/docassemble-AssemblyLine-documentation/docs/generating_code/">"Weaving" your form into a draft interview</a>.
      </p>"""
    
    if jur[0]!="CA":
        
        linkline = "https://apps-dev.suffolklitlab.org/start/ALWeaver/assembly_line?new_session=1&form_to_use=https://courtformsonline.org/forms/%s.pdf"%row["id"] + "&title=" + urllib.parse.quote_plus(row["title"].strip()) + "&jur=%s"%jur[0] + "&nsmi=" + str(nsmi)
        
        html+="""
      <p>
        <a href="%s" target="_blank" class="launch"><div class="launch">Launch Form in Weaver</div></a>
      </p>
      """%(linkline)
    else:
        html+="""
      <p>
        <a href="javascript:alert('Not available for California Forms at this time.')" class="launch"><div class="launch">Launch Form in Weaver</div></a>
      </p>
      """
            
    html+="""
    </div>
  </div>
    """
    return html

In [85]:
# run one sample
path = "../../"
for index,row in files_df[files_df["id"]=="6b4ebd487f82f387512ac20da28803db"].iterrows():
    print(row["jurisdiction"],row["title"])
    
    html = header(row["jurisdiction"]+": "+row["title"],"""We're collecting existing pdf forms from multiple jurisdictions and making it possible for folks (e.g., courts and non-profits) to turn them into beautiful webapps with ease. Eventually, you will be able to go from form to prototype webapp in a few clicks. As time goes by, we'll grow the number of jurisdictions and improve our tools' performance. They'll never do all of the work, but they help plot a course for what otherwise might seem an "impossible" task. They'll help make things concrete, allowing for stakeholders and developers to edit their way to a production-ready solution built on suggestions rooted in years of form building experience.""",path,wide=1)+formview([row["jurisdiction"],""],path)+footer(path)
    text_file = open("docs/form/%s/%s.html"%(row["jurisdiction"],row["id"]), "w", encoding="utf-8")
    
    text_file.write(html)
    text_file.close()

AL Workers' Compensation Notice


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:144: UserWarning: All samples have mutually equal similarities. Returning arbitrary cluster center(s).
  warnings.warn(


In [87]:
%%time

path = "../../"

# comment out if only backfilling
if 1==1:
    for jur in jurs:    
        if not os.path.exists("docs/form/%s"%(jur[0])):
            os.makedirs("docs/form/%s"%(jur[0]))
        else:
            shutil.rmtree("docs/form/%s"%(jur[0]))
            os.makedirs("docs/form/%s"%(jur[0]))
        
print("Start")

loop_df = files_df[files_df["jurisdiction"].isin(list(np.array(jurs)[:, 0]))]
i = 0
p_1 = round(len(loop_df)/100)
for index,row in loop_df.iterrows():
    
    if not os.path.exists("docs/form/%s/%s.html"%(row["jurisdiction"],row["id"])):
        print("{}) {}: {}".format(i,row["jurisdiction"],row["title"]))
        html = header(row["jurisdiction"]+": "+row["title"],"description goes here",path,wide=1)+formview([row["jurisdiction"],""],path)+footer(path)
        text_file = open("docs/form/%s/%s.html"%(row["jurisdiction"],row["id"]), "w", encoding="utf-8")
        text_file.write(html)
        text_file.close()
        
    i += 1
    if i%p_1==0:
        print("\n{}% done...".format(i/p_1))
        governor(0,50,66.66,1)
    else:
        governor(0,50,66.66,0)    

print("END")

Start
0) FL: Instructions For Florida Supreme Court Approved Family Law Form 12.970 (b)


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:250: ConvergenceWarning: Affinity propagation did not converge, this model will not have any cluster centers.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:528: ConvergenceWarning: This model does not have any cluster centers because affinity propagation did not converge. Labeling every sample as '-1'.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:250: ConvergenceWarning: Affinity propagation did not converge, this model will not have any cluster centers.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:528: ConvergenceWarning: This model does not have any cluster centers because affinity propagation did not converge. Labeling every sample as '-1'.
  warnings.wa

1) MN: GAL - Fee Waiver Application (Family)
2) NE: Financial Institution Receipt of Letters
4) SC: Microsoft Word - 516D-- Partial Satisfaction of Judgment
5) SC: Microsoft Word - Document3
6) SD: Affidavit of Military Status
7) KY: (Untitled)
8) RI: Application for Citation in Supplementary Proceedings


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:144: UserWarning: All samples have mutually equal similarities. Returning arbitrary cluster center(s).
  warnings.warn(


9) NC: 
      Juvenile Order - Probable Cause Hearing
    
10) TX: SCOTX Legislative Appropriations Request


...

24702) VT: Department of Health Record of Civil Union Dissolution or Annulment
24703) NC: 
      Nontestimonial Identification Order (Adult Suspect)
    
    Slowing down...
24704) ND: Petitioning for Review of an Unemployment Benefits Decision (Job Service)


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:250: ConvergenceWarning: Affinity propagation did not converge, this model will not have any cluster centers.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:528: ConvergenceWarning: This model does not have any cluster centers because affinity propagation did not converge. Labeling every sample as '-1'.
  warnings.warn(


24705) ID: Subpoena
    Slowing down...
24706) OK: Microsoft Word - form21.rtf
    Slowing down...
24707) IA: 31.25—Form 3 - Registration Statement for Lawyer Engaging in Temporary Practice Following Determination of Major Disaster
    Slowing down...
24708) CT: (Untitled)
24709) CA: Instructions: Abstract of Judgment—Restitution
24710) AK: Flowchart B: After the Case is Started
24711) CO: Download PDF


/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:144: UserWarning: All samples have mutually equal similarities. Returning arbitrary cluster center(s).
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:250: ConvergenceWarning: Affinity propagation did not converge, this model will not have any cluster centers.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:528: ConvergenceWarning: This model does not have any cluster centers because affinity propagation did not converge. Labeling every sample as '-1'.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/python3.8/site-packages/sklearn/cluster/_affinity_propagation.py:250: ConvergenceWarning: Affinity propagation did not converge, this model will not have any cluster centers.
  warnings.warn(
/Users/davidcolarusso/opt/anaconda3/lib/p

24712) NE: INSTRUCTIONS FOR FILLING OUT
24713) NJ: Home Detention Screening Criteria (for Home Detention as a Condition of Pretrial Release)
24714) NV: Microsoft Word - D4F99D126C08CAF6FD5BB80FD7CFFE01.docx
24715) FL: Notice of Confidential Information with Court Filing
    Slowing down...
24716) AK: CIV-853 |  Order on Motion for Judgment on the Pleadings
    Slowing down...
END
CPU times: user 5h 56min 8s, sys: 6min 25s, total: 6h 2min 34s
Wall time: 2h 1min 52s


In [283]:
list(np.array(jurs)[:, 0])

['MA']